In [1]:
from eptnr.graph_generation.problem_graph_generator import ProblemGraphGenerator
from pathlib import Path

# Graph generation

In [2]:
import geopandas as gpd
import os

In [3]:
BASE_PATH = Path('../../eptnr_package/eptnr/datasets/amsterdam_10_2022/')

In [4]:
poi_gdf = gpd.read_file(BASE_PATH / 'non_residential_functions_geojson_latlng_2022.json')
poi_gdf = poi_gdf[poi_gdf.Functie == 'Museum en galerie']
poi_gdf.geometry = gpd.points_from_xy(poi_gdf.geometry.y, poi_gdf.geometry.x, crs='EPSG:4326')
poi_gdf['name'] = poi_gdf['Verblijfsobject']

# Keep only the Rijksmuseum https://www.rijksmuseum.nl/ as a Point of Interest
poi_gdf = poi_gdf[poi_gdf['Verblijfsobject']=='0363010012073352']
poi_gdf

Functie   Verblijfsobject     Functiemix           Adres  \
17876  Museum en galerie  0363010012073352  Voorzieningen  Museumstraat 1   

        Gemeente  Aantal_adressen  Oppervlakte  OPPERVLAKTE_CORRECTIE  \
17876  Amsterdam                1        38149                      0   

             Gebruiksdoel      Objectsoort FUNCTIE_ID FUNCTIEMIX_ID  \
17876  bijeenkomstfunctie  Expositieruimte          G           VZN   

                       geometry              name  
17876  POINT (4.88539 52.35994)  0363010012073352

In [5]:
census_gdf = gpd.read_parquet(BASE_PATH / 'ams_census_and_neighborhood_data_2021.parquet')
census_gdf = gpd.GeoDataFrame(census_gdf[['BU_NAAM', 'res_centroid']], geometry='res_centroid')
census_gdf['name'] = census_gdf['BU_NAAM']
census_gdf

BU_NAAM              res_centroid  \
0                  Kop Zeedijk  POINT (4.90009 52.37552)   
1               Oude Kerk e.o.  POINT (4.89678 52.37375)   
2              Burgwallen Oost  POINT (4.89875 52.37283)   
3                     Nes e.o.  POINT (4.89423 52.37094)   
4              BG-terrein e.o.  POINT (4.89588 52.36999)   
..                         ...                       ...   
443              Gein Zuidwest  POINT (4.98511 52.29471)   
444             Gein Noordoost  POINT (4.99445 52.29913)   
445              Gein Zuidoost  POINT (4.99021 52.29315)   
446              Dorp Driemond  POINT (5.01649 52.30562)   
447  Landelijk gebied Driemond  POINT (5.01314 52.30975)   

                          name  
0                  Kop Zeedijk  
1               Oude Kerk e.o.  
2              Burgwallen Oost  
3                     Nes e.o.  
4              BG-terrein e.o.  
..                         ...  
443              Gein Zuidwest  
444             Gein Noordoost  
445              Gein Zuidoost  
446              Dorp Driemond  
447  Landelijk gebied Driemond  

[448 rows x 3 columns]

In [12]:
city = "Amsterdam"
gtfs_zip_file_path = BASE_PATH / 'full_gtfs_amsterdam_14_10_2022.zip'
out_dir_path = BASE_PATH / 'resulting_graph/'

if not os.path.exists(out_dir_path):
    os.mkdir(out_dir_path)

day = "monday"
time_from = "07:00:00"
time_to = "09:00:00"

modalities = ['metro']

graph_generator = ProblemGraphGenerator(city=city, gtfs_zip_file_path=gtfs_zip_file_path,
                                        out_dir_path=out_dir_path, day=day,
                                        time_from=time_from, time_to=time_to,
                                        agencies=['GVB', 'IFF:GVB'],  # , 'IFF:NS', 'IFF:NSI', 'IFF:RNET'
                                        poi_gdf=poi_gdf, census_gdf=census_gdf, modalities=modalities,
                                        distances_computation_mode='haversine')

graph_generator.generate_problem_graph()

DEBUG:eptnr.graph_generation.problem_graph_generator:Starting GTFS graph generation on 2022-10-18 10:50:30.111612


2022/10/18 10:50:53 [INFO] Saved 1 agency; skipped 34 as unmarked
2022/10/18 10:50:53 [INFO] Saved 78 routes; skipped 2498 as unmarked
2022/10/18 10:50:54 [INFO] Saved 1932 stops; skipped 61130 as unmarked
2022/10/18 10:50:54 [INFO] Saved 0 calendar; generated 31
2022/10/18 10:50:54 [INFO] Saved 343 calendar_dates
2022/10/18 10:50:58 [INFO] Saved 205 shapes; skipped 5755 as unmarked
2022/10/18 10:52:44 [INFO] Saved 34865 trips
2022/10/18 10:52:45 [INFO] Saved 547491 stop_times
2022/10/18 10:52:45 [INFO] Saved 0 transfers; skipped 97081 with reference errors
2022/10/18 10:52:45 [INFO] Saved 1 feed_info
2022/10/18 10:52:45 [INFO] Copied count:
2022/10/18 10:52:45 [INFO] 	agency.txt: 1
2022/10/18 10:52:45 [INFO] 	calendar_dates.txt: 343
2022/10/18 10:52:45 [INFO] 	feed_info.txt: 1
2022/10/18 10:52:45 [INFO] 	routes.txt: 78
2022/10/18 10:52:45 [INFO] 	shapes.txt: 205
2022/10/18 10:52:45 [INFO] 	stop_times.txt: 547491
2022/10/18 10:52:45 [INFO] 	stops.txt: 1932
2022/10/18 10:52:45 [INFO] 	t

INFO:urbanaccess:Checking GTFS text file header whitespace... Reading files using encoding: utf-8 set in configuration.
INFO:urbanaccess:GTFS text file header whitespace check completed. Took 0.04 seconds
INFO:urbanaccess:--------------------------------
INFO:urbanaccess:Processing GTFS feed: resulting_graph


Checking GTFS text file header whitespace... Reading files using encoding: utf-8 set in configuration.
GTFS text file header whitespace check completed. Took 0.04 seconds
--------------------------------
Processing GTFS feed: resulting_graph


INFO:urbanaccess:The unique agency id: gvb was generated using the name of the agency in the agency.txt file.
INFO:urbanaccess:Unique agency id operation complete. Took 0.02 seconds
INFO:urbanaccess:Unique GTFS feed id operation complete. Took 0.00 seconds
INFO:urbanaccess:Records:
INFO:urbanaccess:              stop_id               stop_name  stop_code  stop_desc  \
49    stoparea:344470     Velsen, Velsen Zuid        NaN        NaN   
51      stoparea:2939  Assendelft, Assendelft        NaN        NaN   
196   stoparea:366377     Amsterdam, Westwijk        NaN        NaN   
202   stoparea:344472    Velsen, Velsen Noord        NaN        NaN   
230     stoparea:2940    Spaarndam, Spaarndam        NaN        NaN   
1039          2327658     Amsterdam, Westwijk     7539.0        NaN   
1044          1928480    Velsen, Velsen Noord     9918.0        NaN   
1175          2409638     Amsterdam, Westwijk     7538.0        NaN   
1208          1928479     Velsen, Velsen Zuid     9919.0     

...

stop time table transformation to Pandana format edge table completed. Took 2.29 seconds
Time conversion completed: seconds converted to minutes.
1,211 of 1,921 records selected from stops. Took 0.00 seconds
stop time table transformation to Pandana format node table completed. Took 0.00 seconds


INFO:urbanaccess:route type successfully joined to transit edges. Took 0.35 seconds
INFO:urbanaccess:route id successfully joined to transit edges. Took 0.03 seconds
INFO:urbanaccess:Successfully created transit network. Took 3.50 seconds


route type successfully joined to transit edges. Took 0.35 seconds
route id successfully joined to transit edges. Took 0.03 seconds
Successfully created transit network. Took 3.50 seconds


100%|██████████| 1442/1442 [00:25<00:00, 56.20it/s]
/home/rico/anaconda3/envs/equitable-transport-reduction/lib/python3.9/site-packages/igraph/__init__.py:2988: RuntimeWarning: A non-numeric, non-string, non-boolean graph attribute ignored at src/io/gml.c:677
  return writer(f, *args, **kwds)
DEBUG:eptnr.graph_generation.problem_graph_generator:Created GTFS graph and stored in ../../eptnr_package/eptnr/datasets/amsterdam_10_2022/resulting_graph/Amsterdam_pt_network_monday_20221012_20221210.gml
DEBUG:eptnr.graph_generation.problem_graph_generator:Loading GTFS graph
DEBUG:eptnr.graph_generation.problem_graph_generator:Starting OSM graph generation
DEBUG:eptnr.graph_generation.problem_graph_generator:Created OSM Graph and stored in ../../eptnr_package/eptnr/datasets/amsterdam_10_2022/resulting_graph/Amsterdam_osm_graph_2022-10-18.gpickle
DEBUG:eptnr.graph_generation.problem_graph_generator:Loading OSM graph
DEBUG:eptnr.graph_generation.problem_graph_generator:###
Starting problem graph ge

PosixPath('../../eptnr_package/eptnr/datasets/amsterdam_10_2022/resulting_graph/Amsterdam_problem_graph_2022-10-18.gml')

# Inspection

In [13]:
import igraph as ig

In [14]:
graph: ig.Graph = ig.read('../../eptnr_package/eptnr/datasets/amsterdam_10_2022/resulting_graph/Amsterdam_problem_graph_2022-10-18.gml')

In [15]:
list(graph.es.select(type='METRO'))

[igraph.Edge(<igraph.Graph object at 0x7f8d8454e5e0>, 0, {'type': 'METRO', 'routetype': 1.0, 'name': '480_gvb_5', 'uniquerouteid': '480_gvb', 'uniqueagencyid': 'gvb', 'tt': 2.92, 'weight': 2.91666666666667, 'color': 'BLACK', 'cost': 1142500.0, 'active': 1.0}),
 igraph.Edge(<igraph.Graph object at 0x7f8d8454e5e0>, 1, {'type': 'METRO', 'routetype': 1.0, 'name': '480_gvb_2', 'uniquerouteid': '480_gvb', 'uniqueagencyid': 'gvb', 'tt': 1.77, 'weight': 1.76666666666667, 'color': 'BLACK', 'cost': 400500.0, 'active': 1.0}),
 igraph.Edge(<igraph.Graph object at 0x7f8d8454e5e0>, 2, {'type': 'METRO', 'routetype': 1.0, 'name': '63198_gvb_3', 'uniquerouteid': '63198_gvb', 'uniqueagencyid': 'gvb', 'tt': 1.5, 'weight': 1.5, 'color': 'BLACK', 'cost': 369500.0, 'active': 1.0}),
 igraph.Edge(<igraph.Graph object at 0x7f8d8454e5e0>, 3, {'type': 'METRO', 'routetype': 1.0, 'name': '480_gvb_6', 'uniquerouteid': '480_gvb', 'uniqueagencyid': 'gvb', 'tt': 2.5, 'weight': 2.5, 'color': 'BLACK', 'cost': 603000.0, 

In [17]:
ig.plot(graph.subgraph_edges(graph.es.select(type='METRO')))

In [18]:
graph.es.attributes()

['type',
 'routetype',
 'name',
 'uniquerouteid',
 'uniqueagencyid',
 'tt',
 'weight',
 'color',
 'cost',
 'active']

In [21]:
graph.subgraph_edges(graph.es.select(type='METRO')).es['cost']

[1142500.0,
 400500.0,
 369500.0,
 603000.0,
 634000.0,
 446000.0,
 380500.0,
 635000.0,
 598000.0,
 511000.0,
 391000.0,
 390500.0,
 407500.0,
 602000.0,
 865500.0,
 525000.0,
 622000.0,
 416500.0,
 475000.0,
 1126500.0,
 411000.0,
 408000.0,
 421500.0,
 350500.0,
 390500.0,
 350000.0,
 371000.0,
 328500.0,
 528000.0,
 666000.0,
 666500.0,
 473000.0,
 508500.0,
 754000.0,
 925000.0,
 586000.0,
 553500.0,
 1149500.0,
 544000.0,
 597000.0,
 394000.0,
 394000.0,
 1124500.0,
 312000.0,
 339000.0,
 433000.0,
 361500.0,
 901000.0,
 284000.0,
 549500.0,
 1124500.0,
 545500.0,
 456500.0,
 407500.0,
 754000.0,
 361000.0,
 821000.0,
 765500.0,
 584500.0,
 346500.0,
 543500.0,
 368500.0,
 666500.0,
 321500.0,
 756000.0,
 357000.0,
 433500.0,
 722500.0,
 354500.0,
 475000.0,
 566500.0,
 844000.0,
 548000.0,
 283500.0,
 383500.0,
 351000.0,
 656000.0,
 581500.0,
 539500.0,
 677500.0,
 353500.0,
 369000.0,
 308000.0,
 526000.0,
 387000.0,
 385000.0,
 386000.0,
 384000.0,
 555500.0,
 410000.0,
 5465